In [1]:
import numpy as np
import pandas as pd
import json
import os

import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as pltb

In [2]:
# Example of the data
df = pd.read_csv("data/bike_df.csv")
#print(df[["device.name", "timestamp", "x.acceleration", "y.acceleration", "z.acceleration", "engine.ignition.status.1"]].head().to_markdown(index=False))
df = df[df["device.name"] =="220902-3-3"]

In [ ]:
# Plot the uncalibrated data

x_eye, y_eye, z_eye = 1.5, 1.5, 0

def rotate_z(x, y, z, theta):
    w = x+1j*y
    return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w)

frames=[]
for t in np.arange(0, 6.26, 0.01):
    xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
    frames.append(go.Frame(dict(layout=dict(scene=dict(camera=dict(eye=dict(x=xe, y=ye, z=ze)))))))



fig = go.Figure(
    data=[go.Scatter3d(x=df["x.acceleration"],
    y=df["y.acceleration"],
    z=df["z.acceleration"],
    connectgaps=False,
    mode='markers',
    marker_size=1)],

    layout=go.Layout(
        xaxis=dict(range=[0, 5], autorange=False),
        yaxis=dict(range=[0, 5], autorange=False),
        title="Uncalibrated Data",
        scene=dict(
             xaxis_title='x acceleration',
             yaxis_title='y acceleration',
             zaxis_title='z acceleration'
        ),
        updatemenus=[dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None, {"frame": {"duration": 0.1}, "tranistion": {"duration": 0.1}}])])]
    ),
    frames=frames
)

fig.show()

In [3]:
# First we need to remove nans from the dataset and then center the data.
df.dropna(inplace= True, subset=["x.acceleration", "y.acceleration", "z.acceleration"])

# We wil select an uncalibrated device to perfrom the analysis on
bike_df = df[df["device.name"] =="220902-3-3"]

# We remove all points where the bike is idle as the assumption is only true when the the bike is moving.
bike_df = bike_df[~((bike_df["movement.status"] ==False) | (bike_df["engine.ignition.status"] ==False) | (bike_df["din"] == 0))]

# Select only the acceleratin points
bike_df = bike_df[["x.acceleration", "y.acceleration", "z.acceleration"]]

# Center the data by subtracting the mean
bike_df_centered = bike_df.sub(bike_df.mean(axis=0), axis=1)

bike_df_centered.head()

x.acceleration  y.acceleration  z.acceleration
1        -0.041692        1.606437        2.191783
33        0.113308        1.481760        2.259551
34        0.129308        1.516330        2.254876
35        0.238308        1.581979        2.456726
36        0.129308        1.572611        2.253312

In [4]:
# perform PCA

from sklearn.decomposition import PCA

# We perform the PCA choosing 3 components. This will not reduce the datas dimensions and it is also currently 3 dimentional.
pca = PCA(n_components=3)
principalComponents = pca.fit_transform(bike_df_centered)
print(pca.components_)

[[-0.01534458  0.48943954  0.87190222]
 [ 0.03486902  0.87173642 -0.48873281]
 [-0.99927408  0.02290297 -0.0304427 ]]


In [5]:
# Create new lines for plotting

# We want to visualise the Princple Components on the centered data. We need to transform the x,y,z axis into the axis defined by the principle components
# The values below are x,y,z axis with the uncalibrated basis.
axis_values = np.arange(-3,4)
zero_values = [0]*len(axis_values)
x_axis = np.stack((axis_values, zero_values, zero_values), axis=-1)
y_axis = np.stack((zero_values, axis_values, zero_values), axis=-1)
z_axis = np.stack((zero_values,zero_values, axis_values), axis=-1)

# We transform the x,y,z axis into the new axis.
transformed_axis_x = pca.transform(x_axis)
transformed_axis_y = pca.transform(y_axis)
transformed_axis_z = pca.transform(z_axis) 

NameError: name 'x_values' is not defined

In [119]:
# Plot PCA axis with centered data

x_eye, y_eye, z_eye = 1.5, 1.5, 0

def rotate_z(x, y, z, theta):
    w = x+1j*y
    return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), np.real(np.exp(1j*theta)*w)

frames=[]
for t in np.arange(0, 6.26, 0.01):
    xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
    frames.append(go.Frame(dict(layout=dict(scene=dict(camera=dict(eye=dict(x=xe, y=ye, z=ze)))))))

import math
ndf = bike_df_centered[["x.acceleration", "y.acceleration", "z.acceleration"]].to_numpy()
angle = math.radians(35)
rotation = np.array([[1, 0, 0],
            [0, math.cos(angle), -1*math.sin(angle)],
            [0, math.sin(angle), math.cos(angle)]])
tt = np.matmul(ndf, rotation)
bike_df_centered.loc[:,["x.acceleration", "y.acceleration", "z.acceleration"]] = tt

transformed_axis_x = np.matmul(transformed_axis_x, rotation)
transformed_axis_y = np.matmul(transformed_axis_y, rotation)
transformed_axis_z = np.matmul(transformed_axis_z, rotation) 


fig = go.Figure(
    data=[go.Scatter3d(
    x=bike_df_centered["x.acceleration"],
    y=bike_df_centered["y.acceleration"],
    z=bike_df_centered["z.acceleration"],
    connectgaps=False,
    mode='markers',
    marker_size=1,
    )],
)
# Draw the new lines as figures
figx = px.line_3d(x=transformed_axis_x[:,0], y=transformed_axis_x[:, 1], z=transformed_axis_x[:,2])
figx.update_traces(line_color='#ff0000', line_width=2)
figy = px.line_3d(x=transformed_axis_y[:,0], y=transformed_axis_y[:, 1], z=transformed_axis_y[:,2])
figy.update_traces(line_color='#ff0000', line_width=2)
figz = px.line_3d(x=transformed_axis_z[:,0], y=transformed_axis_z[:, 1], z=transformed_axis_z[:,2])
figz.update_traces(line_color='#ff0000', line_width=2)

# fig3 = go.Figure(data = figx.data + figy.data + figz.data + fig.data,
fig3 = go.Figure(data = fig.data + figx.data + figy.data +  figz.data,
        layout=go.Layout(
            xaxis=dict(range=[0, 5], autorange=False),
            yaxis=dict(range=[0, 5], autorange=False),
            title="Uncalibrated Data",
            scene=dict(
             xaxis_title='x acceleration',
             yaxis_title='y acceleration',
             zaxis_title='z acceleration'
        ),
            updatemenus=[dict(
                type="buttons",
                buttons=[dict(label="Play",
                            method="animate",
                            args=[None, {"frame": {"duration": 0.1}, "tranistion": {"duration": 0.1}}])])]
            ),
        frames=frames
                 
                 
    )
fig3.show()

In [8]:
# plot transformed data

# Transform the data and turn it back into pandas for easy plotting
transformed_df = pca.transform(bike_df_centered)
df_transformed = pd.DataFrame(data=transformed_df, columns = ['x.acceleration', 'y.acceleration', 'z.acceleration'])


x_eye, y_eye, z_eye = 1.5, 1.5, 0

def rotate_z(x, y, z, theta):
    w = x+1j*y
    return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), z

frames=[]
for t in np.arange(0, 6.26, 0.01):
    xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
    frames.append(go.Frame(dict(layout=dict(scene=dict(camera=dict(eye=dict(x=xe, y=ye, z=ze)))))))



fig = go.Figure(
    data=[go.Scatter3d(x=df_transformed["x.acceleration"],
    y=df_transformed["y.acceleration"],
    z=df_transformed["z.acceleration"],
    connectgaps=False,
    mode='markers',
    marker_size=1)],

    layout=go.Layout(
        xaxis=dict(range=[0, 5], autorange=False),
        yaxis=dict(range=[0, 5], autorange=False),
        title="Transformed data",
        scene=dict(
             xaxis_title='x acceleration',
             yaxis_title='y acceleration',
             zaxis_title='z acceleration'
        ),
        updatemenus=[dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None, {"frame": {"duration": 0.1}, "tranistion": {"duration": 0.1}}])])]
    ),
    frames=frames
)

fig.show()

In [23]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(rows=2, cols=2, subplot_titles=('x-y acceleration',  'x-z acceleration', 'y-z acceleration'))

fig.add_trace(
    go.Scatter(x=df_transformed["x.acceleration"], y=df_transformed["y.acceleration"],
        mode='markers',
        marker_size=1),

    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=df_transformed["x.acceleration"], y=df_transformed["z.acceleration"],
        mode='markers',
        marker_size=1),
    row=1, col=2
)

fig.add_trace(
    go.Scatter(x=df_transformed["y.acceleration"], y=df_transformed["z.acceleration"],
        mode='markers',
        marker_size=1),
    row=2, col=1
)

fig.update_layout(height=600, width=800, title_text="2d acceleration view")
fig.update_yaxes(
    range=[-5,5],
    autorange=False,
    scaleanchor="x",
    scaleratio=1,
  )
fig.show()
fig.write_image("images/2dview.png")

ValueError: 
Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido


     |████████████████████████████████| 79.9 MB 111 kB/s eta 0:00:013   |▏                               | 358 kB 3.9 MB/s eta 0:00:21��█████████████████████████▍  | 73.4 MB 8.8 MB/s eta 0:00:01


In [ ]:
# vechile death data
df_death = pd.read_csv("data/List_of_countries_by_traffic-related_death_rate_1.csv", skiprows=[0])
df_death.rename(columns={'per 100,000\ninhabitants\nper year':'Deaths per 100k/year'}, inplace=True)
df_death = df_death[["Country/region", "Continent", "Deaths per 100k/year"]]
df_c = df_death[df_death["Continent"].isnull()].sort_values(by=["Deaths per 100k/year"], ascending=False)
print(df_c[["Country/region", "Deaths per 100k/year"]].to_markdown(index=False))

# find percentile of kenya globally
df_death["Percentile"] = df_death["Deaths per 100k/year"].rank(pct = True)
print(df_death.loc[df_death['Country/region'] == "Kenya"].to_markdown(index=False))

# 
df_a = df_death[df_death["Continent"] == "Africa"].sort_values(by=["Deaths per 100k/year"], ascending=False)
df_a["Percentile"] = df_a["Deaths per 100k/year"].rank(pct = True)
df_a.loc[df_death['Country/region'] == "Kenya"]